In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs
import numpy as np

# set the following to True when connected to hardware:
run_on_hw = False

# instantiate channels representing two AWGs and two digitizers
awgs = qcs.Channels(range(2), "readoutawg")
digs = qcs.Channels(range(2), "readoutreceiver")

# load our channel mapper to connect the virtual channes above to physical ones
mapper = qcs.load("../../assets/channel_mapper.qcs")

In [3]:
# define the frequency and amplitude of our RF waveform as QCS variables
frequency = qcs.Scalar("rf", dtype=float)
amplitude = qcs.Scalar("amp", dtype=float, value=1)


def make_program():
    """Creates a simple program with a single RF waveform"""
    program = qcs.Program()
    # define the waveform using this frequency variable & add it to the program
    gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, frequency)
    program.add_waveform(gauss, awgs)

    # define an integration filter using the same RF waveform but with fixed frequency
    int_filter = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, 4.15e9)
    program.add_acquisition(int_filter, digs)

    # specify the number of shots
    return program.n_shots(10)


program = make_program()

# specify the frequency values to be swept over
frequencies = qcs.Array(
    "frequencies", value=[4.05e9, 4.1e9, 4.15e9, 4.2e9, 4.25e9], dtype=float
)

# add the sweep, targeting the `frequency` variable
program.sweep(frequencies, frequency)

program.draw()

In [4]:
print(program.repetitions.items)

[Sweep(rf=Array(name=frequencies, shape=(5,), dtype=float, unit=none)), Repeat(10)]


In [5]:
if run_on_hw:
    # initialize the backend pass
    backend = qcs.HclBackend(channel_mapper=mapper)
    # the executor returns the program populated with results
    program = qcs.Executor(backend).execute(program)
    # (optional) export the data to an HDF5 file
    program.to_hdf5("program2.hdf5")

# we are loading a previously run program here for this example
program = qcs.load("program2.hdf5")

In [6]:
program.plot_trace()

In [7]:
program.get_iq(stack_channels=True)

(rf, 4.05 GHz)  \
                                                                     0   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000191-0.003899j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.004437-0.001820j   

                                                                        \
                                                                     1   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000077-0.003642j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.002133-0.001429j   

                                                                        \
                                                                     2   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000430-0.004168j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.002552-0.000963j   

                                                                        \
                                                                     3   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000012-0.004071j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.003809-0.001938j   

                                                                        \
                                                                     4   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000042-0.003658j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.002047-0.001594j   

                                                                        \
                                                                     5   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000510-0.004211j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.002233-0.000374j   

                                                                        \
                                                                     6   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000052-0.004175j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.004006-0.001622j   

                                                                        \
                                                                     7   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000084-0.003701j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.002390-0.001392j   

                                                                        \
                                                                     8   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000719-0.004324j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.002402-0.000332j   

                                                                        ...  \
                                                                     9  ...   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000124-0.004373j  ...   
(((Channels(labels=[1], name=readoutreceiver, a... -0.004073-0.001305j  ...   

                                                        (rf, 4.25 GHz)  \
                                                                     0   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000036+0.000368j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.000378-0.000470j   

                                                                        \
                                                                     1   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000318-0.000300j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.000537+0.000370j   

                                                                        \
                                                                     2   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000000-0.000124j   
(((Channels(labels=[1], name=readoutreceiver, a...  0.000590-0.000199j   

                                                                        \
                                                                     3   
(((Channels(labels=[0], nam

In [8]:
df = program.get_iq(stack_channels=True)
channel0_rf_4_05_data = df["(rf, 4.05 GHz)"]["0"][digs[0]]
print(channel0_rf_4_05_data)

(-0.00019140228972316692-0.003898978610783353j)


In [9]:
program.results.get_iq()[digs[0]]

array([[-1.91402290e-04-3.89897861e-03j,  7.70289665e-05-3.64209390e-03j,
        -4.30160632e-04-4.16754846e-03j,  1.20284667e-05-4.07141253e-03j,
         4.15836104e-05-3.65753864e-03j, -5.09600539e-04-4.21130410e-03j,
        -5.21141851e-05-4.17486558e-03j,  8.39615156e-05-3.70079315e-03j,
        -7.19177847e-04-4.32388577e-03j, -1.23657266e-04-4.37293974e-03j],
       [-1.66186861e-02+3.47513473e-03j,  1.13629142e-02+1.27458832e-02j,
         5.42432161e-03-1.59696063e-02j, -1.65766110e-02+3.34303555e-03j,
         1.12454880e-02+1.26769889e-02j,  5.42309369e-03-1.61666690e-02j,
        -1.67368608e-02+3.48733935e-03j,  1.14300947e-02+1.26495161e-02j,
         5.36066815e-03-1.61397442e-02j, -1.67338263e-02+3.46158123e-03j],
       [ 1.68788959e-01-3.11123121e-02j,  1.68708986e-01-3.11430939e-02j,
         1.68702229e-01-3.09507697e-02j,  1.68736191e-01-3.11747065e-02j,
         1.69111285e-01-3.11912603e-02j,  1.68753332e-01-3.08776137e-02j,
         1.68991335e-01-3.12165456e-

In [10]:
program.plot_iq(channel_subplots=False)

In [11]:
new_frequencies = qcs.Array(
    "rfs", value=np.linspace(4.05e9, 4.25e9, num=20), dtype=float
)

program = make_program()
program.sweep(new_frequencies, frequency)

if run_on_hw:
    # initialize the backend pass
    # setting hw_demod=True enables hardware demodulation of trace data
    backend = qcs.HclBackend(channel_mapper=mapper, hw_demod=True)
    # the executor returns the program populated with results
    program = qcs.Executor(backend).execute(program)
    # (optional) export the data to an HDF5 file
    program.to_hdf5("program3.hdf5")

# we are loading a previously run program here for this example
program = qcs.load("program3.hdf5")

program.plot_iq(channel_subplots=False)

In [12]:
program.get_classified()

(((Channels(labels=[0], name=readoutreceiver, absolute_phase=False))))     \
                                                          (rf, 4.05 GHz)      
                                                                       0  1   
0                                                  1                      1   

                           ...  \
                           ...   
   2  3  4  5  6  7  8  9  ...   
0  1  1  1  1  1  1  1  1  ...   

  (((Channels(labels=[1], name=readoutreceiver, absolute_phase=False))))     \
                                                          (rf, 4.25 GHz)      
                                                                       0  1   
0                                                  1                      0   

                           
                           
   2  3  4  5  6  7  8  9  
0  1  1  0  1  0  0  1  1  

[1 rows x 400 columns]

In [13]:
program.plot_classified(channel_subplots=False)

In [14]:
program = qcs.load("program4.hdf5")

In [15]:
program.plot_classified(avg=True, plot_type="2d")

In [16]:
program = make_program()

# specify the frequency values to be swept over
frequencies = qcs.Array(
    "frequencies", value=[4.05e9, 4.1e9, 4.15e9, 4.2e9, 4.25e9], dtype=float
)

# specify the amplitude values to be swept over
amplitudes = qcs.Array("amplitude", value=[0.2, 0.4, 0.6, 0.8, 1], dtype=float)

program.sweep(frequencies, frequency)
program.sweep(amplitudes, amplitude)

print(program.repetitions.items)

[Sweep(amp=Array(name=amplitude, shape=(5,), dtype=float, unit=none)), Sweep(rf=Array(name=frequencies, shape=(5,), dtype=float, unit=none)), Repeat(10)]


In [17]:
if run_on_hw:
    program = qcs.Executor(qcs.HclBackend(mapper, hw_demod=True)).apply(program)
    program.to_hdf5("program4.hdf5")

program = qcs.load("program4.hdf5")

program.get_iq(avg=True, stack_channels=True)

(amp, 0.2)  \
                                                        (rf, 4.05 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000005+0.000003j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.000121-0.000029j   

                                                                        \
                                                         (rf, 4.1 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000331-0.000086j   
(((Channels(labels=[1], name=readoutreceiver, a...  0.000231+0.000307j   

                                                                        \
                                                        (rf, 4.15 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a...  0.037200-0.005492j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.035342-0.020230j   

                                                                        \
                                                         (rf, 4.2 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000265+0.000231j   
(((Channels(labels=[1], name=readoutreceiver, a...  0.000409+0.000025j   

                                                                        \
                                                        (rf, 4.25 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000040+0.000042j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.000028-0.000068j   

                                                            (amp, 0.4)  \
                                                        (rf, 4.05 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000073-0.000376j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.000321-0.000335j   

                                                                        \
                                                         (rf, 4.1 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000585-0.000206j   
(((Channels(labels=[1], name=readoutreceiver, a...  0.000420+0.000575j   

                                                                        \
                                                        (rf, 4.15 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a...  0.073275-0.011098j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.069978-0.039586j   

                                                                        \
                                                         (rf, 4.2 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000518+0.000330j   
(((Channels(labels=[1], name=readoutreceiver, a...  0.000692+0.000120j   

                                                                        ...  \
                                                        (rf, 4.25 GHz)  ...   
(((Channels(labels=[0], name=readoutreceiver, a... -0.000065-0.000038j  ...   
(((Channels(labels=[1], name=readoutreceiver, a... -0.000064-0.000022j  ...   

                                                            (amp, 0.8)  \
                                                        (rf, 4.05 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a...  0.000320-0.002474j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.002400-0.001459j   

                                                                        \
                                                         (rf, 4.1 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a... -0.001304-0.000108j   
(((Channels(labels=[1], name=readoutreceiver, a...  0.001120+0.000956j   

                                                                        \
                                                        (rf, 4.15 GHz)   
(((Channels(labels=[0], name=readoutreceiver, a...  0.140380-0.023565j   
(((Channels(labels=[1], name=readoutreceiver, a... -0.135962-0.074133j   

                                                                        \
                                                         (rf, 4.2 GHz)   
(((Channels(labels=[0], name=re

In [18]:
# plot over amplitude for each frequency
program.plot_iq(channel_subplots=False)

In [19]:
# plot over frequency for each amplitude
program.plot_iq(channel_subplots=False, plot_axis=1)

In [20]:
program = make_program()

# specify the frequency values to be swept over
frequencies = qcs.Array(
    "frequencies", value=[4.05e9, 4.1e9, 4.15e9, 4.2e9, 4.25e9], dtype=float
)

# specify the amplitude values to be swept over
amplitudes = qcs.Array("amplitude", value=[0.2, 0.4, 0.6, 0.8, 1], dtype=float)

program.sweep([frequencies, amplitudes], [frequency, amplitude])

Program([Layer(Channels(labels=[0, 1], name=readoutawg, absolute_phase=False)=[RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=_implicit, value=1.0, dtype=float, unit=none)}, rf_frequency=Scalar(name=rf, value=None, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))], Channels(labels=[0, 1], name=readoutreceiver, absolute_phase=False)=[Acquisition(IntegrationFilter(RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=_implicit, value=1.0, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4150000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, un

In [21]:
if run_on_hw:
    program = qcs.Executor(qcs.HclBackend(mapper, hw_demod=True)).apply(program)
    program.to_hdf5("program5.hdf5")

program = qcs.load("program5.hdf5")

program.get_iq(avg=True, stack_channels=True)

(rf, 4.05 GHz), (amp, 0.2)  \
(((Channels(labels=[0], name=readoutreceiver, a...          0.000013-0.000013j   
(((Channels(labels=[1], name=readoutreceiver, a...         -0.000073-0.000024j   

                                                    (rf, 4.1 GHz), (amp, 0.4)  \
(((Channels(labels=[0], name=readoutreceiver, a...        -0.000613-0.000192j   
(((Channels(labels=[1], name=readoutreceiver, a...         0.000425+0.000622j   

                                                    (rf, 4.15 GHz), (amp, 0.6)  \
(((Channels(labels=[0], name=readoutreceiver, a...          0.107115-0.017246j   
(((Channels(labels=[1], name=readoutreceiver, a...         -0.103357-0.057106j   

                                                    (rf, 4.2 GHz), (amp, 0.8)  \
(((Channels(labels=[0], name=readoutreceiver, a...        -0.000988+0.000395j   
(((Channels(labels=[1], name=readoutreceiver, a...         0.001224+0.000277j   

                                                    (rf, 4.25 GHz), (amp, 1)  
(((Channels(labels=[0], name=readoutreceiver, a...        0.000078-0.000041j  
(((Channels(labels=[1], name=readoutreceiver, a...       -0.000104-0.000037j

In [22]:
# plot the results
program.plot_iq(channel_subplots=False)

In [23]:
frequency = qcs.Scalar("rf", dtype=float)

"""Creates a simple program with a single RF waveform"""
program = qcs.Program()
# define the waveform using this frequency variable & add it to the program
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, frequency)
program.add_waveform(gauss, awgs)

# define an integration filter using the same RF waveform but with fixed frequency
int_filter = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, 4.15e9)
program.add_acquisition(int_filter, digs)

# specify the frequency values to be swept over
frequencies = qcs.Array(
    "frequencies", value=[4.05e9, 4.1e9, 4.15e9, 4.2e9, 4.25e9], dtype=float
)

# add the sweep, targeting the `frequency` variable
program.sweep(frequencies, frequency)

# specify the number of shots
program.n_shots(10)

program.draw()

In [24]:
program.repetitions.hw_items

[Repeat(10),
 Sweep(rf=Array(name=frequencies, shape=(5,), dtype=float, unit=none))]

In [25]:
amplitude = qcs.Scalar("amp", dtype=float)

program = qcs.Program()

# define the waveform using this frequency variable & add it to the program
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude, 4e9)
program.add_waveform(gauss, awgs)

# define the values for the sweep
amplitudes = qcs.Array("amplitudes", value=np.linspace(0.1, 0.2, 10000), dtype=float)

# sweep the program
program.sweep(amplitudes, amplitude)
program.n_shots(10)

Program([Layer([RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))])])

In [26]:
frequency = qcs.Scalar("rf", dtype=float)
amplitude = qcs.Scalar("amp", dtype=float)

program = qcs.Program()

# define the waveform using this frequency variable & add it to the program
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude, frequency)
program.add_waveform(gauss, awgs)

# define the values for each sweep
frequencies = qcs.Array(
    "frequencies", value=np.linspace(4e9, 4.1e9, 10000), dtype=float
)
amplitudes = qcs.Array("amplitudes", value=np.linspace(0.1, 0.2, 10000), dtype=float)

# sweep the program
program.sweep(frequencies, frequency)
program.sweep(amplitudes, amplitude)
program.n_shots(10)

Program([Layer([RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=rf, value=None, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))])])

In [27]:
amplitude1 = qcs.Scalar("amp", dtype=float)

program = qcs.Program()

# define the waveform using this frequency variable & add it to the program
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude, 4e9)
program.add_waveform(gauss, awgs)
program.add_waveform(gauss, awgs, pre_delay=20e-9)
program.add_waveform(gauss, awgs, pre_delay=20e-9)
# define the values for the sweep
amplitudes = qcs.Array("amplitudes", value=np.linspace(0.1, 0.2, 10000), dtype=float)

# sweep the program
program.sweep(amplitudes, amplitude)
program.n_shots(10)

Program([Layer([RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)), Delay(Scalar(name=_implicit, value=2e-08, dtype=float, unit=s)), RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)), Delay(Scalar(name=_implicit, value=2e-08, dtype=float, unit=s)), RFWaveform(duratio

In [28]:
amplitude1 = qcs.Scalar("amp1", dtype=float)
amplitude2 = qcs.Scalar("amp2", dtype=float)

program = qcs.Program()

# define the waveform using this frequency variable & add it to the program
gauss1 = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude1, 4e9)
gauss2 = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude2, 4e9)
program.add_waveform(gauss1, awgs)
program.add_waveform(gauss2, awgs)

# define the values for the sweep
amplitudes1 = qcs.Array("amplitudes1", value=np.linspace(0.1, 0.2, 10000), dtype=float)
amplitudes2 = qcs.Array("amplitudes2", value=np.linspace(0.3, 0.4, 10000), dtype=float)

# sweep the program
program.sweep([amplitudes1, amplitudes2], [amplitude1, amplitude2])
program.n_shots(10)

Program([Layer([RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp1, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)), RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp2, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))])])